In [1]:
import pandas as pd 
import plotly.express as px
import hvplot.pandas
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler,OneHotEncoder
from sklearn.decomposition import PCA
import datetime 

In [5]:
inventory_df = pd.read_csv("../Resources/ml_housing_inventory_clean.csv")
inventory_df.head()

Unnamed: 0    REF_DATE       Completed_units          Dwelling_Type  \
0           0  1988-06-01           Absorptions    Semi-detached units   
1           1  1988-06-01           Absorptions  Single detached units   
2           2  1988-06-01  Unabsorbed inventory    Semi-detached units   
3           3  1988-06-01  Unabsorbed inventory  Single detached units   
4           4  1988-07-01           Absorptions    Semi-detached units   

   Abbotsford-Mission  Barrie  Brantford  Calgary  Edmonton  Greater Sudbury  \
0                 3.0     0.0        0.0      2.0      22.0              0.0   
1                74.0    84.0       45.0    136.0     256.0             19.0   
2                 2.0     0.0        0.0      5.0      14.0              0.0   
3                64.0    12.0       35.0    165.0     138.0             10.0   
4                 2.0     0.0        0.0     16.0      20.0              0.0   

   ...  Sherbrooke  St. Catharines-Niagara  St. John's  Thunder Bay  Toronto  \
0  ...         3.0                    12.0         0.0          2.0     42.0   
1  ...        58.0                    73.0       100.0         47.0   1965.0   
2  ...        14.0                    33.0         0.0          2.0     10.0   
3  ...        57.0                   240.0        45.0          1.0    294.0   
4  ...         0.0                    18.0         0.0          0.0     93.0   

   Trois-Rivières  Vancouver  Victoria  Windsor  Winnipeg  
0            22.0       69.0       1.0      0.0       4.0  
1            85.0      626.0      85.0     67.0     373.0  
2            12.0       86.0       4.0      0.0       0.0  
3            82.0      722.0     108.0     37.0     138.0  
4             5.0       59.0       0.0      0.0       6.0  

[5 rows x 38 columns]

In [6]:
inventory_df=inventory_df.set_index('REF_DATE')
inventory_df=inventory_df.drop('Unnamed: 0',axis=1)
inventory_df.head()

Completed_units          Dwelling_Type  Abbotsford-Mission  \
REF_DATE                                                                      
1988-06-01           Absorptions    Semi-detached units                 3.0   
1988-06-01           Absorptions  Single detached units                74.0   
1988-06-01  Unabsorbed inventory    Semi-detached units                 2.0   
1988-06-01  Unabsorbed inventory  Single detached units                64.0   
1988-07-01           Absorptions    Semi-detached units                 2.0   

            Barrie  Brantford  Calgary  Edmonton  Greater Sudbury  Guelph  \
REF_DATE                                                                    
1988-06-01     0.0        0.0      2.0      22.0              0.0     0.0   
1988-06-01    84.0       45.0    136.0     256.0             19.0    22.0   
1988-06-01     0.0        0.0      5.0      14.0              0.0     0.0   
1988-06-01    12.0       35.0    165.0     138.0             10.0     1.0   
1988-07-01     0.0        0.0     16.0      20.0              0.0     0.0   

            Halifax  ...  Sherbrooke  St. Catharines-Niagara  St. John's  \
REF_DATE             ...                                                   
1988-06-01     35.0  ...         3.0                    12.0         0.0   
1988-06-01     93.0  ...        58.0                    73.0       100.0   
1988-06-01    197.0  ...        14.0                    33.0         0.0   
1988-06-01    138.0  ...        57.0                   240.0        45.0   
1988-07-01     52.0  ...         0.0                    18.0         0.0   

            Thunder Bay  Toronto  Trois-Rivières  Vancouver  Victoria  \
REF_DATE                                                                
1988-06-01          2.0     42.0            22.0       69.0       1.0   
1988-06-01         47.0   1965.0            85.0      626.0      85.0   
1988-06-01          2.0     10.0            12.0       86.0       4.0   
1988-06-01          1.0    294.0            82.0      722.0     108.0   
1988-07-01          0.0     93.0             5.0       59.0       0.0   

            Windsor  Winnipeg  
REF_DATE                       
1988-06-01      0.0       4.0  
1988-06-01     67.0     373.0  
1988-06-01      0.0       0.0  
1988-06-01     37.0     138.0  
1988-07-01      0.0       6.0  

[5 rows x 36 columns]

In [7]:
# Find duplicated entries 
inventory_df = inventory_df.drop_duplicates()
print(f"Duplication entries: {inventory_df.duplicated().sum()}")


Duplication entries: 0


In [8]:
# Generate our categorical variable list
cat = inventory_df.dtypes[inventory_df.dtypes == "object"].index.tolist()

In [15]:
# Begining encoding with OneHotEncoder
# Create a OneHotEncoder instance
enc = OneHotEncoder(sparse=False)

# Fit and transform the OneHotEncoder using the categorical variable list
encode_df = pd.DataFrame(enc.fit_transform(inventory_df[cat]),index=inventory_df.index)

# Add the encoded variable names to the DataFrame
encode_df.columns = enc.get_feature_names(cat)
encode_df.head()

Completed_units_Absorptions  Completed_units_Unabsorbed inventory  \
REF_DATE                                                                        
1988-06-01                          1.0                                   0.0   
1988-06-01                          1.0                                   0.0   
1988-06-01                          0.0                                   1.0   
1988-06-01                          0.0                                   1.0   
1988-07-01                          1.0                                   0.0   

            Dwelling_Type_Semi-detached units  \
REF_DATE                                        
1988-06-01                                1.0   
1988-06-01                                0.0   
1988-06-01                                1.0   
1988-06-01                                0.0   
1988-07-01                                1.0   

            Dwelling_Type_Single detached units  
REF_DATE                                         
1988-06-01                                  0.0  
1988-06-01                                  1.0  
1988-06-01                                  0.0  
1988-06-01                                  1.0  
1988-07-01                                  0.0

In [11]:
len(encode_df)

1544

In [12]:
len(inventory_df)

1544

In [34]:
# Merge one-hot encoded features and drop the originals
# final_df = pd.concat([inventory_df,encode_df], axis = 1)
final_df = pd.merge(inventory_df,encode_df,left_on=inventory_df.index, right_on=encode_df.index)
final_df = final_df.drop(cat,1)
final_df=final_df.set_index('key_0')
final_df.index.name = None
final_df.head()

Abbotsford-Mission  Barrie  Brantford  Calgary  Edmonton  \
1988-06-01                 3.0     0.0        0.0      2.0      22.0   
1988-06-01                 3.0     0.0        0.0      2.0      22.0   
1988-06-01                 3.0     0.0        0.0      2.0      22.0   
1988-06-01                 3.0     0.0        0.0      2.0      22.0   
1988-06-01                74.0    84.0       45.0    136.0     256.0   

            Greater Sudbury  Guelph  Halifax  Hamilton  Kelowna  ...  Toronto  \
1988-06-01              0.0     0.0     35.0       2.0      0.0  ...     42.0   
1988-06-01              0.0     0.0     35.0       2.0      0.0  ...     42.0   
1988-06-01              0.0     0.0     35.0       2.0      0.0  ...     42.0   
1988-06-01              0.0     0.0     35.0       2.0      0.0  ...     42.0   
1988-06-01             19.0    22.0     93.0     205.0     86.0  ...   1965.0   

            Trois-Rivières  Vancouver  Victoria  Windsor  Winnipeg  \
1988-06-01            22.0       69.0       1.0      0.0       4.0   
1988-06-01            22.0       69.0       1.0      0.0       4.0   
1988-06-01            22.0       69.0       1.0      0.0       4.0   
1988-06-01            22.0       69.0       1.0      0.0       4.0   
1988-06-01            85.0      626.0      85.0     67.0     373.0   

            Completed_units_Absorptions  Completed_units_Unabsorbed inventory  \
1988-06-01                          1.0                                   0.0   
1988-06-01                          1.0                                   0.0   
1988-06-01                          0.0                                   1.0   
1988-06-01                          0.0                                   1.0   
1988-06-01                          1.0                                   0.0   

            Dwelling_Type_Semi-detached units  \
1988-06-01                                1.0   
1988-06-01                                0.0   
1988-06-01                                1.0   
1988-06-01                                0.0   
1988-06-01                                1.0   

            Dwelling_Type_Single detached units  
1988-06-01                                  0.0  
1988-06-01                                  1.0  
1988-06-01                                  0.0  
1988-06-01                                  1.0  
1988-06-01                                  0.0  

[5 rows x 38 columns]

In [35]:
for column in final_df.columns:
    print(f'Colum {column} has {final_df[column].isnull().sum()} null values')
    

Colum Abbotsford-Mission has 0 null values
Colum Barrie has 0 null values
Colum Brantford has 0 null values
Colum Calgary has 0 null values
Colum Edmonton has 0 null values
Colum Greater Sudbury has 0 null values
Colum Guelph has 0 null values
Colum Halifax has 0 null values
Colum Hamilton has 0 null values
Colum Kelowna has 0 null values
Colum Kingston has 0 null values
Colum Kitchener-Cambridge-Waterloo has 0 null values
Colum London has 0 null values
Colum Moncton has 0 null values
Colum Montréal has 1840 null values
Colum Montréal excluding Saint-Jérôme has 4336 null values
Colum Oshawa has 0 null values
Colum Ottawa-Gatineau has 0 null values
Colum Peterborough has 0 null values
Colum Québec has 0 null values
Colum Regina has 0 null values
Colum Saguenay has 0 null values
Colum Saint John has 0 null values
Colum Saskatoon has 0 null values
Colum Sherbrooke has 0 null values
Colum St. Catharines-Niagara has 0 null values
Colum St. John's has 0 null values
Colum Thunder Bay has 0 nu

In [36]:
final_df=final_df.drop(['Montréal','Montréal excluding Saint-Jérôme'],axis=1)

In [45]:
final_df.to_csv('../Resources/ml_inventory_data.csv')

In [52]:
# Standarize data with StandardScaler 
data_scaled = StandardScaler().fit_transform(final_df)


In [53]:
# Initialize PCA model
pca = PCA(n_components=4)

In [54]:
# Get two principal components for the iris data.
data_pca = pca.fit_transform(data_scaled)

In [55]:
# Transform PCA data to a DataFrame 
df_data_pca = pd.DataFrame(
    data=data_pca, columns=["PC1", "PC2", "PC3",'PC4'])
df_data_pca.head()

PC1       PC2       PC3       PC4
0 -4.476556  0.074945 -0.377184 -1.002569
1 -4.476556  0.074946 -0.377182  1.730642
2 -4.476556  0.074945 -0.377175 -1.730275
3 -4.476556  0.074946 -0.377173  1.002936
4  7.792370  4.235446  2.292883 -1.001322

In [56]:
# Fetch the explained variance 
pca.explained_variance_ratio_

array([0.44875415, 0.09415066, 0.058433  , 0.05555555])

In [42]:
# Find the best value for K
inertia = []
k = list(range(1, 11))

# Calculate the inertia for the range of K values
for i in k:
	km = KMeans(n_clusters=i, random_state=0)
	km.fit(df_data_pca)
	inertia.append(km.inertia_)

# Create the elbow curve
elbow_data = {"k": k, "inertia": inertia}
df_elbow = pd.DataFrame(elbow_data)
df_elbow.hvplot.line(x="k", y="inertia", xticks=k, title="Elbow Curve")

:Curve   [k]   (inertia)

In [50]:
# Initialize the K-means model
model = KMeans(n_clusters=6, random_state=0)

# Fit the model
model.fit(df_data_pca)

# Predict clusters
predictions = model.predict(df_data_pca)

# Add the predicted class columns
df_data_pca["class"] = model.labels_
df_data_pca.head()

PC1       PC2       PC3  class
0 -4.476556  0.074962 -0.377066      1
1 -4.476556  0.074962 -0.377066      1
2 -4.476556  0.074962 -0.377066      1
3 -4.476556  0.074962 -0.377066      1
4  7.792369  4.235546  2.292423      4

In [51]:
# Plotting the clusters with three features 
fig = px.scatter_3d(df_data_pca, x= "PC1", y= "PC2", z="PC3", color= "class", symbol = "class", size = "class", width=800)
fig.update_layout(legend=dict(x=0,y=1))
fig.show()